
## Etude des patients d'une assurance

## 1. Chargement du dataset

In [0]:
from pyspark.sql.functions import sum, col
from pyspark.ml.feature import Imputer

from pyspark.ml.feature import VectorAssembler
from pyspark.ml.clustering import KMeans

from pyspark.sql import SparkSession
from pyspark.ml.feature import VectorAssembler, StringIndexer
from pyspark.ml import Pipeline
from pyspark.ml.classification import RandomForestClassifier
from pyspark.ml.evaluation import MulticlassClassificationEvaluator

from pyspark.ml.regression import RandomForestRegressor
from pyspark.ml.evaluation import RegressionEvaluator

In [0]:
# Le chemin d'accès au dataset
file_location = "/FileStore/tables/effectifs-1.csv"
file_type = "csv"

# CSV options
infer_schema = "true"
first_row_is_header = "true"
delimiter = ";"

# Le chargement du dataset
df = spark.read.format(file_type) \
  .option("inferSchema", infer_schema) \
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)




In [0]:
df.display(2)

annee patho_niv1 patho_niv2 patho_niv3 top cla_age_5 sexe region dept Ntop Npop prev Niveau prioritaire libelle_classe_age libelle_sexe tri 2020 Maladies cardioneurovasculaires Maladie valvulaire Maladie valvulaire MCV_MVA_IND 75-79 1 1 971 70 6150 1.154 2,3 de 75 à 79 ans hommes 31.0 2020 Maladies cardioneurovasculaires Maladie valvulaire Maladie valvulaire MCV_MVA_IND 75-79 1 2 972 90 6100 1.459 2,3 de 75 à 79 ans hommes 31.0 2020 Maladies cardioneurovasculaires Maladie valvulaire Maladie valvulaire MCV_MVA_IND 75-79 1 3 973 20 1270 1.579 2,3 de 75 à 79 ans hommes 31.0 2020 Maladies cardioneurovasculaires Maladie valvulaire Maladie valvulaire MCV_MVA_IND 75-79 1 3 999 20 1270 1.579 2,3 de 75 à 79 ans hommes 31.0 2020 Maladies cardioneurovasculaires Maladie valvulaire Maladie valvulaire MCV_MVA_IND 75-79 1 6 999 null 480 null 2,3 de 75 à 79 ans hommes 31.0 2020 Maladies cardioneurovasculaires Maladie valvulaire Maladie valvulaire MCV_MVA_IND 75-79 1 11 78 550 19360 2.856 2,3 de 75 à 79 ans hommes 31.0 2020 Maladies cardioneurovasculaires Maladie valvulaire Maladie valvulaire MCV_MVA_IND 75-79 1 11 91 430 15390 2.781 2,3 de 75 à 79 ans hommes 31.0 2020 Maladies cardioneurovasculaires Maladie valvulaire Maladie valvulaire MCV_MVA_IND 75-79 1 11 92 470 18470 2.523 2,3 de 75 à 79 ans hommes 31.0 2020 Maladies cardioneurovasculaires Maladie valvulaire Maladie valvulaire MCV_MVA_IND 75-79 1 24 18 160 5910 2.74 2,3 de 75 à 79 ans hommes 31.0 2020 Maladies cardioneurovasculaires Maladie valvulaire Maladie valvulaire MCV_MVA_IND 75-79 1 24 28 210 6330 3.381 2,3 de 75 à 79 ans hommes 31.0 2020 Maladies cardioneurovasculaires Maladie valvulaire Maladie valvulaire MCV_MVA_IND 75-79 1 24 36 160 4440 3.624 2,3 de 75 à 79 ans hommes 31.0 2020 Maladies cardioneurovasculaires Maladie valvulaire Maladie valvulaire MCV_MVA_IND 75-79 1 24 41 180 5950 3.074 2,3 de 75 à 79 ans hommes 31.0 2020 Maladies cardioneurovasculaires Maladie valvulaire Maladie valvulaire MCV_MVA_IND 75-79 1 27 21 290 8480 3.383 2,3 de 75 à 79 ans hommes 31.0 2020 Maladies cardioneurovasculaires Maladie valvulaire Maladie valvulaire MCV_MVA_IND 75-79 1 27 39 180 4800 3.793 2,3 de 75 à 79 ans hommes 31.0 2020 Maladies cardioneurovasculaires Maladie valvulaire Maladie valvulaire MCV_MVA_IND 75-79 1 27 58 120 4130 2.952 2,3 de 75 à 79 ans hommes 31.0 2020 Maladies cardioneurovasculaires Maladie valvulaire Maladie valvulaire MCV_MVA_IND 75-79 1 27 71 450 10730 4.212 2,3 de 75 à 79 ans hommes 31.0 2020 Maladies cardioneurovasculaires Maladie valvulaire Maladie valvulaire MCV_MVA_IND 75-79 1 28 14 390 10790 3.605 2,3 de 75 à 79 ans hommes 31.0 2020 Maladies cardioneurovasculaires Maladie valvulaire Maladie valvulaire MCV_MVA_IND 75-79 1 28 61 200 4900 4.039 2,3 de 75 à 79 ans hommes 31.0 2020 Maladies cardioneurovasculaires Maladie valvulaire Maladie valvulaire MCV_MVA_IND 75-79 1 28 999 2010 50540 3.967 2,3 de 75 à 79 ans hommes 31.0 2020 Maladies cardioneurovasculaires Maladie valvulaire Maladie valvulaire MCV_MVA_IND 75-79 1 32 59 1010 28850 3.508 2,3 de 75 à 79 ans hommes 31.0 2020 Maladies cardioneurovasculaires Maladie valvulaire Maladie valvulaire MCV_MVA_IND 75-79 1 32 999 2540 72210 3.511 2,3 de 75 à 79 ans hommes 31.0 2020 Maladies cardioneurovasculaires Maladie valvulaire Maladie valvulaire MCV_MVA_IND 75-79 1 44 55 110 2780 3.81 2,3 de 75 à 79 ans hommes 31.0 2020 Maladies cardioneurovasculaires Maladie valvulaire Maladie valvulaire MCV_MVA_IND 75-79 1 44 08 190 3980 4.854 2,3 de 75 à 79 ans hommes 31.0 2020 Maladies cardioneurovasculaires Maladie valvulaire Maladie valvulaire MCV_MVA_IND 75-79 1 44 88 280 6010 4.576 2,3 de 75 à 79 ans hommes 31.0 2020 Maladies cardioneurovasculaires Maladie valvulaire Maladie valvulaire MCV_MVA_IND 75-79 1 52 44 650 19020 3.433 2,3 de 75 à 79 ans hommes 31.0 2020 Maladies cardioneurovasculaires Maladie valvulaire Maladie valvulaire MCV_MVA_IND 75-79 1 52 72 270 8900 3.058 2,3 de 75 à 79 ans hommes 31.0 2020 Maladies cardioneurovascul

## 2. Exploration des données

* L'effectif total

In [0]:
df.count()

Out[4]: 4636800

In [0]:
df.printSchema()

root
 |-- annee: integer (nullable = true)
 |-- patho_niv1: string (nullable = true)
 |-- patho_niv2: string (nullable = true)
 |-- patho_niv3: string (nullable = true)
 |-- top: string (nullable = true)
 |-- cla_age_5: string (nullable = true)
 |-- sexe: integer (nullable = true)
 |-- region: integer (nullable = true)
 |-- dept: string (nullable = true)
 |-- Ntop: integer (nullable = true)
 |-- Npop: integer (nullable = true)
 |-- prev: double (nullable = true)
 |-- Niveau prioritaire: string (nullable = true)
 |-- libelle_classe_age: string (nullable = true)
 |-- libelle_sexe: string (nullable = true)
 |-- tri: double (nullable = true)



In [0]:
df.columns

Out[5]: ['annee',
 'patho_niv1',
 'patho_niv2',
 'patho_niv3',
 'top',
 'cla_age_5',
 'sexe',
 'region',
 'dept',
 'Ntop',
 'Npop',
 'prev',
 'Niveau prioritaire',
 'libelle_classe_age',
 'libelle_sexe',
 'tri']

## 3. Netoyage du dataset

In [0]:
# Suppression de la variable tri qui est moyen important
df = df.drop("tri")
df.columns

Out[6]: ['annee',
 'patho_niv1',
 'patho_niv2',
 'patho_niv3',
 'top',
 'cla_age_5',
 'sexe',
 'region',
 'dept',
 'Ntop',
 'Npop',
 'prev',
 'Niveau prioritaire',
 'libelle_classe_age',
 'libelle_sexe']

#### - Gestion des valeurs manquantes

In [0]:
# Verifier les valeurs manquantes
missing_values_count = df.select([sum(col(c).isNull().cast("int")).alias(c) for c in df.columns])
missing_values_count.show()

+-----+----------+----------+----------+---+---------+----+------+----+-------+----+-------+------------------+------------------+------------+
|annee|patho_niv1|patho_niv2|patho_niv3|top|cla_age_5|sexe|region|dept|   Ntop|Npop|   prev|Niveau prioritaire|libelle_classe_age|libelle_sexe|
+-----+----------+----------+----------+---+---------+----+------+----+-------+----+-------+------------------+------------------+------------+
|    0|         0|    483840|   1048320|  0|        0|   0|     0|   0|1238024|   0|1238024|             60480|                 0|           0|
+-----+----------+----------+----------+---+---------+----+------+----+-------+----+-------+------------------+------------------+------------+



- Il y a 483 840 valeurs manquantes dans colonne patho_niv2, 1 048 320 dans la colonne, 1 238 024 dans ntop et prev et 60 480

In [0]:
# Imputation par la moyenne de la colonne

# Spécifier les colonnes à imputer
imputer = Imputer(inputCols=['Ntop', 'prev'], outputCols=["Ntop_imputed", "prev_imputed"])

# Appliquer l'imputation
imputer_model = imputer.fit(df)
data_imputed = imputer_model.transform(df)

# Afficher un échantillon des données imputées
data_imputed.show(5)

+-----+--------------------+------------------+------------------+-----------+---------+----+------+----+----+----+-----+------------------+------------------+------------+------------+-----------------+
|annee|          patho_niv1|        patho_niv2|        patho_niv3|        top|cla_age_5|sexe|region|dept|Ntop|Npop| prev|Niveau prioritaire|libelle_classe_age|libelle_sexe|Ntop_imputed|     prev_imputed|
+-----+--------------------+------------------+------------------+-----------+---------+----+------+----+----+----+-----+------------------+------------------+------------+------------+-----------------+
| 2020|Maladies cardione...|Maladie valvulaire|Maladie valvulaire|MCV_MVA_IND|    75-79|   1|     1| 971|  70|6150|1.154|               2,3|    de 75 à 79 ans|      hommes|          70|            1.154|
| 2020|Maladies cardione...|Maladie valvulaire|Maladie valvulaire|MCV_MVA_IND|    75-79|   1|     2| 972|  90|6100|1.459|               2,3|    de 75 à 79 ans|      hommes|          90

In [0]:
# Supprimer les anciennes colonnes
data_imputed = data_imputed.drop('Ntop', 'prev')

# Renommer les colonnes imputées
data_imputed = data_imputed.withColumnRenamed("Ntop_imputed", "Ntop") \
                           .withColumnRenamed("prev_imputed", "prev")

# Afficher un échantillon des données finales
data_imputed.show(5)

+-----+--------------------+------------------+------------------+-----------+---------+----+------+----+----+------------------+------------------+------------+----+-----------------+
|annee|          patho_niv1|        patho_niv2|        patho_niv3|        top|cla_age_5|sexe|region|dept|Npop|Niveau prioritaire|libelle_classe_age|libelle_sexe|Ntop|             prev|
+-----+--------------------+------------------+------------------+-----------+---------+----+------+----+----+------------------+------------------+------------+----+-----------------+
| 2020|Maladies cardione...|Maladie valvulaire|Maladie valvulaire|MCV_MVA_IND|    75-79|   1|     1| 971|6150|               2,3|    de 75 à 79 ans|      hommes|  70|            1.154|
| 2020|Maladies cardione...|Maladie valvulaire|Maladie valvulaire|MCV_MVA_IND|    75-79|   1|     2| 972|6100|               2,3|    de 75 à 79 ans|      hommes|  90|            1.459|
| 2020|Maladies cardione...|Maladie valvulaire|Maladie valvulaire|MCV_MVA_I

In [0]:
# Imputation des valeurs manquantes pour les colonnes catégorielles

# Trouver la valeur la plus fréquente pour la colonne catégorielle 'patho_niv2'
mode_patho_niv2_row = df.groupBy("patho_niv2").count().orderBy("count", ascending=False).first()

# Si mode_patho_niv2_row est None, choisir une valeur par défaut pour l'imputation
if mode_patho_niv2_row is not None:
    mode_patho_niv2 = mode_patho_niv2_row[0]
else:
    mode_patho_niv2 = "Unknown"  # ou une autre valeur par défaut appropriée



# Vérifier que la colonne 'patho_niv2' est présente dans le DataFrame et appliquer l'imputation
if 'patho_niv2' in data_imputed.columns and mode_patho_niv2 is not None:
    data_imputed = data_imputed.fillna({"patho_niv2": mode_patho_niv2})
else:
    print("La colonne 'patho_niv2' n'est pas présente dans le DataFrame ou mode_dept est None.")


# Afficher un échantillon des données finales
data_imputed.show(5)


La colonne 'patho_niv2' n'est pas présente dans le DataFrame ou mode_dept est None.
+-----+--------------------+------------------+------------------+-----------+---------+----+------+----+----+------------------+------------------+------------+
|annee|          patho_niv1|        patho_niv2|        patho_niv3|        top|cla_age_5|sexe|region|dept|Npop|Niveau prioritaire|libelle_classe_age|libelle_sexe|
+-----+--------------------+------------------+------------------+-----------+---------+----+------+----+----+------------------+------------------+------------+
| 2020|Maladies cardione...|Maladie valvulaire|Maladie valvulaire|MCV_MVA_IND|    75-79|   1|     1| 971|6150|               2,3|    de 75 à 79 ans|      hommes|
| 2020|Maladies cardione...|Maladie valvulaire|Maladie valvulaire|MCV_MVA_IND|    75-79|   1|     2| 972|6100|               2,3|    de 75 à 79 ans|      hommes|
| 2020|Maladies cardione...|Maladie valvulaire|Maladie valvulaire|MCV_MVA_IND|    75-79|   1|     3| 973|1

In [0]:
# Trouver la valeur la plus fréquente pour la colonne catégorielle 'patho_niv3'
mode_patho_niv3_row = df.groupBy("patho_niv3").count().orderBy("count", ascending=False).first()

# Si mode_patho_niv3_row est None, choisir une valeur par défaut pour l'imputation
if mode_patho_niv3_row is not None:
    mode_patho_niv3 = mode_patho_niv2_row[0]
else:
    mode_patho_niv3 = "Unknown"  # ou une autre valeur par défaut appropriée


# Vérifier que la colonne 'patho_niv3' est présente dans le DataFrame et appliquer l'imputation
if 'patho_niv3' in data_imputed.columns and mode_patho_niv3 is not None:
    data_imputed = data_imputed.fillna({"patho_niv3": mode_patho_niv3})
else:
    print("La colonne 'patho_niv3' n'est pas présente dans le DataFrame ou mode_dept est None.")

data_imputed.show(5)

La colonne 'patho_niv3' n'est pas présente dans le DataFrame ou mode_dept est None.
+-----+--------------------+------------------+------------------+-----------+---------+----+------+----+----+------------------+------------------+------------+
|annee|          patho_niv1|        patho_niv2|        patho_niv3|        top|cla_age_5|sexe|region|dept|Npop|Niveau prioritaire|libelle_classe_age|libelle_sexe|
+-----+--------------------+------------------+------------------+-----------+---------+----+------+----+----+------------------+------------------+------------+
| 2020|Maladies cardione...|Maladie valvulaire|Maladie valvulaire|MCV_MVA_IND|    75-79|   1|     1| 971|6150|               2,3|    de 75 à 79 ans|      hommes|
| 2020|Maladies cardione...|Maladie valvulaire|Maladie valvulaire|MCV_MVA_IND|    75-79|   1|     2| 972|6100|               2,3|    de 75 à 79 ans|      hommes|
| 2020|Maladies cardione...|Maladie valvulaire|Maladie valvulaire|MCV_MVA_IND|    75-79|   1|     3| 973|1

### - Gestion des doublons

In [0]:
data_imputed.groupBy(data_imputed.columns).count().filter("count > 1").show()

+-----+----------+----------+----------+---+---------+----+------+----+----+------------------+------------------+------------+-----+
|annee|patho_niv1|patho_niv2|patho_niv3|top|cla_age_5|sexe|region|dept|Npop|Niveau prioritaire|libelle_classe_age|libelle_sexe|count|
+-----+----------+----------+----------+---+---------+----+------+----+----+------------------+------------------+------------+-----+
+-----+----------+----------+----------+---+---------+----+------+----+----+------------------+------------------+------------+-----+



Pas de doublons dans le dataset

## 3. Statistiques descriptive

In [0]:
data_imputed.columns

Out[84]: ['annee',
 'patho_niv1',
 'patho_niv2',
 'patho_niv3',
 'top',
 'cla_age_5',
 'sexe',
 'region',
 'dept',
 'Npop',
 'Niveau prioritaire',
 'libelle_classe_age',
 'libelle_sexe',
 'Ntop',
 'prev']

In [0]:
# Statistiques descriptives
data_imputed['Ntop','Npop','prev'].describe().show()

+-------+------------------+------------------+------------------+
|summary|              Ntop|              Npop|              prev|
+-------+------------------+------------------+------------------+
|  count|           4636800|           4636800|           4636800|
|   mean| 5527.314623878537|103045.67958505866|6.2105446769700166|
| stddev|136120.97979478177| 987420.8102856627|13.670531090144216|
|    min|                10|                10|               0.0|
|    max|          68729230|          68729230|             100.0|
+-------+------------------+------------------+------------------+



In [0]:
# Distribution des pathologies
data_imputed.groupBy('patho_niv1').count().orderBy('count', ascending=False).show()



+--------------------+------+
|          patho_niv1| count|
+--------------------+------+
|Maladies cardione...|907200|
|             Cancers|846720|
|Maladies inflamma...|665280|
|Maladies neurolog...|483840|
|Maladies psychiat...|423360|
|Traitements psych...|302400|
|Insuffisance réna...|241920|
|Traitements du ri...|181440|
|Hospitalisations ...| 60480|
|Traitement antalg...| 60480|
|Maladies du foie ...| 60480|
|Maladies respirat...| 60480|
|Pas de pathologie...| 60480|
|             Diabète| 60480|
|Affections de lon...| 60480|
|Hospitalisation p...| 60480|
|Total consommants...| 60480|
|Maternité (avec o...| 40320|
+--------------------+------+



In [0]:
# Distribution des traitements
data_imputed.groupBy('top').count().orderBy('count', ascending=False).show()



+-----------+-----+
|        top|count|
+-----------+-----+
|PSY_AUT_IND|60480|
|INF_VIH_IND|60480|
|NEU_AUT_IND|60480|
|NEU_CAT_CAT|60480|
|NEU_SEP_IND|60480|
|IFL_CAT_CAT|60480|
|TAA_CAT_EXC|60480|
|TPS_ANX_EXC|60480|
|CAN_AUT_SUR|60480|
|CAN_CAT_CAT|60480|
|CAN_CRE_ACT|60480|
|MCV_TRC_IND|60480|
|RAR_MMH_IND|60480|
|RAR_MUC_IND|60480|
|INF_COV_HOS|60480|
|PSY_PSC_IND|60480|
|NEU_LME_IND|60480|
|MCV_ICA_CHR|60480|
|MCV_SCO_AIG|60480|
|CAN_CRE_CAT|60480|
+-----------+-----+
only showing top 20 rows



In [0]:
# Distribution des épisodes de soins par sexe
data_imputed.groupBy('sexe', 'patho_niv1').count().orderBy('count', ascending=False).show()

+----+--------------------+------+
|sexe|          patho_niv1| count|
+----+--------------------+------+
|   9|             Cancers|322560|
|   9|Maladies cardione...|302400|
|   2|Maladies cardione...|302400|
|   1|Maladies cardione...|302400|
|   1|             Cancers|262080|
|   2|             Cancers|262080|
|   1|Maladies inflamma...|221760|
|   2|Maladies inflamma...|221760|
|   9|Maladies inflamma...|221760|
|   2|Maladies neurolog...|161280|
|   1|Maladies neurolog...|161280|
|   9|Maladies neurolog...|161280|
|   9|Maladies psychiat...|141120|
|   1|Maladies psychiat...|141120|
|   2|Maladies psychiat...|141120|
|   2|Traitements psych...|100800|
|   9|Traitements psych...|100800|
|   1|Traitements psych...|100800|
|   2|Insuffisance réna...| 80640|
|   9|Insuffisance réna...| 80640|
+----+--------------------+------+
only showing top 20 rows



### - Analyse des effectif


In [0]:
# Effectif  moyens des patients par pathologie
data_imputed.groupBy('patho_niv1').agg({'Ntop': 'mean'}).orderBy('avg(Ntop)', ascending=False).show()
# Effectif moyens des patients par région
data_imputed.groupBy('region').agg({'Ntop': 'mean'}).orderBy('avg(Ntop)', ascending=False).show()
# Effectifs moyens des patients par sexe
data_imputed.groupBy('sexe').agg({'Ntop': 'mean'}).orderBy('avg(Ntop)', ascending=False).show()


+--------------------+------------------+
|          patho_niv1|         avg(Ntop)|
+--------------------+------------------+
|Total consommants...|104346.08713624338|
|Pas de pathologie...| 57272.23275462963|
|Hospitalisations ...|15241.879034391535|
|Traitements du ri...| 10788.68595127866|
|             Diabète|6454.1861607142855|
|Maternité (avec o...| 6451.100446428572|
|Maladies respirat...| 5754.756332671957|
|Traitements psych...| 4905.632374338625|
|Hospitalisation p...| 4153.309837962963|
|Insuffisance réna...| 3508.559697420635|
|Maladies cardione...|3193.5732374338622|
|             Cancers| 3035.936789021164|
|Affections de lon...|2690.8360945767195|
|Maladies psychiat...| 2355.628384826153|
|Maladies neurolog...| 2316.067117228836|
|Traitement antalg...| 2140.725562169312|
|Maladies inflamma...| 2127.415449134199|
|Maladies du foie ...|1651.3635912698412|
+--------------------+------------------+

+------+------------------+
|region|         avg(Ntop)|
+------+-----------

### -  Analyse de la Prévalence

In [0]:
# Prévalence par région
data_imputed.groupBy('region').agg({'prev': 'mean'}).orderBy('avg(prev)', ascending=False).show()

# Prévalence par sexe
data_imputed.groupBy('sexe').agg({'prev': 'mean'}).orderBy('avg(prev)', ascending=False).show()

# Prévalence par classe d’âge
data_imputed.groupBy('cla_age_5').agg({'prev': 'mean'}).orderBy('avg(prev)', ascending=False).show()

+------+------------------+
|region|         avg(prev)|
+------+------------------+
|     6| 7.706160267455661|
|    94| 6.974250287626114|
|     3| 6.780251105482901|
|    27| 6.465414715762425|
|    76|6.4303725971543955|
|    75| 6.370152984585502|
|    44| 6.320078609839641|
|    24| 6.215354596226064|
|    28| 6.166548184367123|
|    84| 6.138740445337267|
|    93| 6.080857116758874|
|     1| 6.024482054220722|
|    32| 5.992706345841737|
|    53| 5.980439771709703|
|    52| 5.966899103140376|
|     2| 5.939810189406547|
|     4|5.6544682205559385|
|    11| 5.575356363355479|
|    99| 4.871028679850539|
+------+------------------+

+----+------------------+
|sexe|         avg(prev)|
+----+------------------+
|   1| 6.477294173806387|
|   2|6.2683430309217645|
|   9|5.9016980040186855|
+----+------------------+

+---------+------------------+
|cla_age_5|         avg(prev)|
+---------+------------------+
|    95et+|10.596802029666394|
|    90-94|10.007348925898176|
|    85-89| 9.126

## Segmentation des Patients



In [0]:
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.clustering import KMeans

# Préparer les données
assembler = VectorAssembler(inputCols=['annee', 'sexe', 'region', 'Ntop', 'Npop', 'prev'], outputCol="features")
data_assembled = assembler.transform(data_imputed)

# K-Means Clustering
kmeans = KMeans().setK(5).setSeed(1)
model = kmeans.fit(data_assembled.select('features'))

# Prédictions
predictions = model.transform(data_assembled)

# Montrer les clusters
predictions.groupBy('prediction').count().show()

+----------+-------+
|prediction|  count|
+----------+-------+
|         1|    560|
|         4|  51487|
|         2|   1264|
|         0|4583473|
|         3|     16|
+----------+-------+



### Preparation des données pour la construction des modèles de prédiction 

In [0]:
# Préparer les données : indexer les colonnes catégorielles et assembler les caractéristiques
indexers = [StringIndexer(inputCol=column, outputCol=column+"_index") for column in data_imputed.columns]
assembler = VectorAssembler(inputCols=['annee', 'patho_niv1_index', 'patho_niv2_index', 'patho_niv3_index', 'top_index', 'cla_age_5_index', 'sexe', 'region', 'dept_index', 'Ntop', 'Npop', 'prev', 'niveau_prioritaire_index', 'libelle_classe_age_index', 'libelle_sexe_index'], outputCol="features")


### - Segmentation des Patients


In [0]:

#Utiliser des techniques de clustering pour segmenter les patients en groupes homogènes basés sur leurs caractéristiques.

from pyspark.ml.feature import VectorAssembler
from pyspark.ml.clustering import KMeans

# Préparer les données
assembler = VectorAssembler(inputCols=['annee', 'sexe', 'region', 'Ntop', 'Npop', 'prev'], outputCol="features")
data_assembled = assembler.transform(data_imputed)

# K-Means Clustering
kmeans = KMeans().setK(5).setSeed(1)
model = kmeans.fit(data_assembled.select('features'))

# Prédictions
predictions = model.transform(data_assembled)

# Montrer les clusters
predictions.groupBy('prediction').count().show()


+----------+-------+
|prediction|  count|
+----------+-------+
|         1|    560|
|         4|  51487|
|         2|   1264|
|         0|4583473|
|         3|     16|
+----------+-------+



### - Separation des données en ensemble d'entrainement et de test

In [0]:
# Diviser les données en train et test
(trainingData, testData) = data_imputed.randomSplit([0.8, 0.2], seed=1234)

### Construire un model de régression pour la classification des patient, a fin de pouvoir predire sa pathologie 

In [0]:
# Créer le modèle RandomForest
rf = RandomForestClassifier(labelCol="sexe", featuresCol="features", numTrees=10, maxBins=110)

# Construire le pipeline
pipeline = Pipeline(stages=indexers + [assembler, rf])

# Entraîner le modèle
model = pipeline.fit(trainingData)

# Faire des prédictions
predictions = model.transform(testData)


#### Evaluation du model de randmForest

In [0]:
# Évaluer le modèle
evaluator = MulticlassClassificationEvaluator(labelCol="sexe", predictionCol="prediction", metricName="accuracy")
accuracy = evaluator.evaluate(predictions)
print(f"Accuracy: {accuracy}")


Accuracy: 1.0


### Construire un model de régression pour prédire la prévalence

In [0]:
# Créer le modèle RandomForestRegressor avec maxBins augmenté
rf = RandomForestRegressor(labelCol="prev", featuresCol="features", numTrees=10, maxBins=110)

# Construire le pipeline
pipeline = Pipeline(stages=indexers + [assembler, rf])

# Entraîner le modèle
model = pipeline.fit(trainingData)

# Faire des prédictions
predictions = model.transform(testData)

#### Evaluation du model de Régression pour la prédiction de la prévalence

In [0]:
# Évaluer le modèle du model de regression
evaluator = RegressionEvaluator(labelCol="prev", predictionCol="prediction", metricName="rmse")
rmse = evaluator.evaluate(predictions)
print(f"RMSE: {rmse}")


RMSE: 3.0184577931445453
